# Add Traffic Signals to Network
In this case we already have a traffic signal inventory from the Georgia Department of Transportation, but code for downloading existing traffic signal data from OpenStreetMap (OSM) is also included. This code also retrieves crossings from OSM.

In [23]:
from pathlib import Path 
import geopandas as gpd

In [24]:
network_fp = Path.home() / 'Documents/BikewaySimData/Projects/gdot/networks'
links = gpd.read_file(network_fp/'filtered.gpkg',layer='osm_links')
nodes = gpd.read_file(network_fp/'filtered.gpkg',layer='osm_nodes')

links.rename(columns={'osm_A':'A','osm_B':'B','osm_linkid':'linkid'},inplace=True)
nodes.rename(columns={'osm_N':'N'},inplace=True)

In [25]:
signals_fp = Path.home() / 'Documents/BikewaySimData/Data/GDOT/traffic_signals.geojson'
keep = ['signalID','mainStreetName','sideStreetName','geometry']
signals = gpd.read_file(signals_fp).to_crs(links.crs)[keep]
signals = signals.clip(links.total_bounds)

### First we set a buffer distance around each signal to find all candidate nodes associated with the traffic signal.

In [26]:
dist = 150
signals.set_geometry('geometry',inplace=True)
signals['buffered_geo'] = signals.buffer(dist)
signals.set_geometry('buffered_geo',inplace=True)
signals.explore()

### Next, we intersect these bufferred signals with the street nodes

In [27]:
intersect = gpd.overlay(nodes,signals,how='intersection')
intersect = intersect[['N','signalID']]#,'mainStreetName','sideStreetName']]
intersect = dict(zip(intersect['N'],intersect['signalID']))

### Most signals should only be at the intersection of public roads (and maybe a parking lot entrance), knowing this subset to only look at public roads and then calculate the degree of the road nodes. Remove signal id matches for links with degree of 2 or less.

In [28]:
only_roads = links['link_type']=='road'
road_nodes = links['A'].append(links['B']).value_counts()
#remove matches where degree is 2 or less
road_nodes = road_nodes[road_nodes>2].index.tolist()
intersect = {key:item for key, item in intersect.items() if key in road_nodes}

### With that done, we assign the signal ID to the node and add it as an attribute in links

In [29]:
links['signal_A'] = links['A'].map(intersect)
links['signal_B'] = links['B'].map(intersect)
nodes['signalid'] = nodes['N'].map(intersect)

Drop null values

In [30]:
links = links[~links[['signal_A','signal_B']].isna().all(axis=1)]
nodes = nodes[~nodes['N'].isna()]

## In the Export Network notebook, we'll process this data further

In [31]:
links.to_file(network_fp/'signals_added.gpkg',layer='links')
nodes.to_file(network_fp/'signals_added.gpkg',layer='nodes')